In [100]:
from langchain.prompts.few_shot import FewShotPromptTemplate
from langchain.prompts.prompt import PromptTemplate
from langchain.prompts.example_selector import SemanticSimilarityExampleSelector
from langchain.vectorstores import Chroma
from langchain.embeddings import OpenAIEmbeddings
from langchain.llms import OpenAI

In [101]:
examples = [
    {"question":"天气怎么样", "answer":"晴"},
    {"question":"北京天气怎么样", "answer":"加法"},
    {"question":"咋样", "answer":"加法"},
    {"question":"天儿咋样", "answer":"加法"},
    {"question":"今天有雾", "answer":"加法"},
    {"question":"吃得怎么样", "answer":"加法"},
    {"question":"你叫什么", "answer":"加法"},
    {"question":"你叫嘿嘿", "answer":"加法"},
    {"question":"是吗", "answer":"加法"},
    {"question":"10-1=9", "answer":"作业帮回答：减法"},
    {"question":"9-1=8", "answer":"作业帮回答：减法"},
    {"question":"8-1=7", "answer":"作业帮回答：减法"},
    {"question":"7-1=6", "answer":"作业帮回答：减法"},
    {"question":"7-2=5", "answer":"作业帮回答：减法"},
    {"question":"10-3=7", "answer":"作业帮回答：减法"},
    {"question":"10-4=6", "answer":"作业帮回答：减法"},
    {"question":"10-5=5", "answer":"作业帮回答：减法"},
    {"question":"10+5=15", "answer":"作业帮回答：加法"},
    {"question":"10*5=50", "answer":"作业帮回答：乘法"},
    {"question":"10/5=2", "answer":"作业帮回答：除法"},
]

In [102]:
example_selector = SemanticSimilarityExampleSelector.from_examples(
    # This is the list of examples available to select from.
    examples,
    # This is the embedding class used to produce embeddings which are used to measure semantic similarity.
    OpenAIEmbeddings(),
    # This is the VectorStore class that is used to store the embeddings and do a similarity search over.
    Chroma,
    # This is the number of examples to produce.
    k=1
)

Using embedded DuckDB without persistence: data will be transient


In [103]:
example_prompt = PromptTemplate(input_variables=["question", "answer"], template="Question: {question}\n{answer}")

In [104]:
prompt = FewShotPromptTemplate(
    example_selector=example_selector, 
    example_prompt=example_prompt, 
    suffix="Question: {input}", 
    input_variables=["input"]
)

print(prompt.format(input="1+2=？"))

Question: 10+5=15
作业帮回答：加法

Question: 1+2=？


In [105]:
llm = OpenAI(temperature=0)
llm(prompt.format(input="天气怎么样"))

'？\n很晴朗，非常适合出去活动。'